In [ ]:
import openai
from llama_index import SimpleDirectoryReader
from llama_index import Document
from llama_index import VectorStoreIndex
from llama_index import ServiceContext
from llama_index.llms import OpenAI

from llama_index.embeddings import HuggingFaceEmbedding
from llama_index import StorageContext, load_index_from_storage

import time

### Run Indexing in memory without using vectorstore

In [ ]:
start_time = time.time()

In [ ]:
documents = SimpleDirectoryReader(input_files=["../raw_documents/HI_Knowledge_Base.pdf"]).load_data()
document = Document(text="\n\n".join([doc.text for doc in documents]))

In [ ]:
llm = OpenAI(model="gpt-3.5-turbo-1106", temperature=0.1)

In [ ]:
embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")

In [ ]:
# service_context = ServiceContext.from_defaults(llm=llm, embed_model=embed_model)
service_context = ServiceContext.from_defaults(llm=None, embed_model=embed_model)
index = VectorStoreIndex.from_documents([document], service_context=service_context)

In [ ]:
indexing_cost = time.time() - start_time
indexing_cost = indexing_cost / 60
print(f"indexing time: {indexing_cost:.1f} mins")

In [ ]:
index.storage_context.persist(persist_dir="../models/llama_index_json/")

In [ ]:
query_engine = index.as_query_engine()

In [ ]:
response = query_engine.query("What is medishield")

In [ ]:
print(str(response))

### Load index from persisted file without using vectorstore

In [ ]:
start_time = time.time()

In [ ]:
embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")

In [ ]:
service_context = ServiceContext.from_defaults(llm=None, embed_model=embed_model)

In [ ]:
storage_context = StorageContext.from_defaults(persist_dir="../models/llama_index_json/")

In [ ]:
index = load_index_from_storage(storage_context=storage_context, service_context=service_context)

In [ ]:
load_indexing_cost = time.time() - start_time
load_indexing_cost = load_indexing_cost / 60
print(f"Load indexing time: {load_indexing_cost:.1f} mins")

### Instantiate query engine

In [ ]:
query_engine = index.as_query_engine()

In [ ]:
response = query_engine.query("What is medishield")
print(str(response))

### ChromaDB method - create vectorstore

In [ ]:
import chromadb
from llama_index import VectorStoreIndex, SimpleDirectoryReader
from llama_index.vector_stores import ChromaVectorStore
from llama_index.storage.storage_context import StorageContext
from llama_index import ServiceContext
from llama_index import Document

from llama_index.embeddings import HuggingFaceEmbedding

import time

In [ ]:
# load some documents
documents = SimpleDirectoryReader(input_files=["../raw_documents/HI_Knowledge_Base.pdf"]).load_data()
document = Document(text="\n\n".join([doc.text for doc in documents]))

In [ ]:
# initialize client, setting path to save data
db = chromadb.PersistentClient(path="../models/chroma_db")

In [ ]:
# create collection
chroma_collection = db.get_or_create_collection("quickstart")

In [ ]:
# assign chroma as the vector_store to the context
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)

In [ ]:
embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")

In [ ]:
service_context = ServiceContext.from_defaults(llm=None, embed_model=embed_model)

In [ ]:
storage_context = StorageContext.from_defaults(vector_store=vector_store)

In [ ]:
start_time = time.time()

In [ ]:
# create your index
index = VectorStoreIndex.from_documents(
    documents, service_context=service_context, storage_context=storage_context
)

In [ ]:
indexing_cost = time.time() - start_time
indexing_cost = indexing_cost / 60
print(f"Indexing time: {indexing_cost:.1f} mins")

In [ ]:
# create a query engine and query
query_engine = index.as_query_engine()

In [ ]:
retriever = index.as_retriever()

In [ ]:
r_list = retriever.retrieve("What is the meaning of life?")

In [ ]:
r_list[1].to_dict()

In [ ]:
response = query_engine.query("What is the meaning of life?")

In [ ]:
print(response)

### ChromaDB method - load vectorstore

In [ ]:
import chromadb
from llama_index import VectorStoreIndex, SimpleDirectoryReader
from llama_index.vector_stores import ChromaVectorStore
from llama_index.storage.storage_context import StorageContext
from llama_index import ServiceContext
from llama_index import Document

from llama_index.embeddings import HuggingFaceEmbedding

import time

In [ ]:
embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")

In [ ]:
service_context = ServiceContext.from_defaults(llm=None, embed_model=embed_model)

In [ ]:
db = chromadb.PersistentClient(path="../models/chroma_db")

In [ ]:
chroma_collection = db.get_or_create_collection("quickstart")

In [ ]:
# assign chroma as the vector_store to the context
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)
storage_context = StorageContext.from_defaults(vector_store=vector_store)

In [ ]:
# create your index
index = VectorStoreIndex.from_vector_store(
    vector_store=vector_store, service_context=service_context, storage_context=storage_context
)

In [ ]:
# create a query engine
query_engine = index.as_query_engine()

In [ ]:
response = query_engine.query("What is llama2?")
print(response)